In [1]:
import pandas as pd
from gnews import GNews
import nltk
from nltk.corpus import PlaintextCorpusReader
from nltk.corpus import stopwords
from nltk.stem.porter import *
from nltk import pos_tag, word_tokenize
from nltk.stem import WordNetLemmatizer
from nltk.probability import FreqDist
from nltk.tokenize import sent_tokenize
from nltk.tokenize import word_tokenize
import contractions

import gensim
from gensim import corpora
from gensim import similarities
from gensim import models
from gensim.models import CoherenceModel

# from wordcloud import WordCloud, ImageColorGenerator
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
import re
import os
import glob
import json

import psycopg2
import pickle
from datetime import datetime
import datetime

In [2]:
# !pip3 install GNews

In [3]:
# Function to get full news article by headline
def get_news_article(headline):
    # Initialize GNews client
    gnews = GNews()

    articles = gnews.get_news(headline)

    # Check if any articles were found
    results = []

    if articles:
        for link in range(len(articles)):
            try:
                article = gnews.get_full_article(articles[link]["url"])
                if article.text:
                    results.append([article.url, article.title, article.text])
                    break

            except Exception as e:
                # link cannot be scraped
                continue

        if not results:
            # if blocked by the website
            results.append(
                [
                    "cannot scrape the url",
                    "cannot scrape the title",
                    "cannot scrape the content",
                ]
            )

    # No articles found for the given title.
    else:
        results.append(["no url found", "no title found", "no content found"])

    return results

In [4]:
# Read the CSV file with news titles
csv_file_path = "LDA/cleaned_data.csv"
df = pd.read_csv(csv_file_path)

In [5]:
df.shape

(5782, 17)

In [6]:
# drop empty news
df.dropna(subset=["Headline"], inplace=True)

In [7]:
df[["Year", "Headline", "Region"]].duplicated().any()

True

In [8]:
# drop the duplicated news
duplicates = df.duplicated(subset=["Year", "Headline", "Region"], keep="first")
df_uni = df[~duplicates]

In [9]:
df_uni.shape

(5710, 17)

In [ ]:
print(datetime.datetime.now())

In [10]:
# Iterate through each row and get the full news article
tes = df_uni
for index, row in tes.iterrows():
    headline = row["Headline"]

    results = get_news_article(headline)

    # Update the DataFrame with the fetched data
    tes.at[index, "url"] = results[0][0]
    tes.at[index, "title"] = results[0][1]
    tes.at[index, "content"] = results[0][2]

<ipython-input-10-19127b23eaff>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tes.at[index, 'url'] = results[0][0]
<ipython-input-10-19127b23eaff>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tes.at[index, 'title'] = results[0][1]
<ipython-input-10-19127b23eaff>:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user

An error occurred while fetching the article: Article `download()` failed with 401 Client Error: HTTP Forbidden for url: https://www.reuters.com/world/china/major-container-ports-eastern-china-see-worsening-congestion-after-covid-cases-2021-08-12/ on URL https://news.google.com/rss/articles/CBMifmh0dHBzOi8vd3d3LnJldXRlcnMuY29tL3dvcmxkL2NoaW5hL21ham9yLWNvbnRhaW5lci1wb3J0cy1lYXN0ZXJuLWNoaW5hLXNlZS13b3JzZW5pbmctY29uZ2VzdGlvbi1hZnRlci1jb3ZpZC1jYXNlcy0yMDIxLTA4LTEyL9IBAA?oc=5&hl=en-SG&gl=SG&ceid=SG:en
An error occurred while fetching the article: Article `download()` failed with 401 Client Error: HTTP Forbidden for url: https://www.reuters.com/article/britain-equinor-oil-strike-idUKL8N1UG4QA/ on URL https://news.google.com/rss/articles/CBMiSWh0dHBzOi8vd3d3LnJldXRlcnMuY29tL2FydGljbGUvYnJpdGFpbi1lcXVpbm9yLW9pbC1zdHJpa2UtaWRVS0w4TjFVRzRRQS_SAQA?oc=5&hl=en-SG&gl=SG&ceid=SG:en
An error occurred while fetching the article: Article `download()` failed with 403 Client Error: Forbidden for url: http

03/11/2024 11:42:16 AM - fromstring() returned an invalid string: <!DOCTYPE html>
<htm...


An error occurred while fetching the article: Article `download()` failed with 401 Client Error: HTTP Forbidden for url: https://www.reuters.com/world/asia-pacific/typhoon-doksuri-shuts-businesses-grounds-flights-taiwan-2023-07-27/ on URL https://news.google.com/rss/articles/CBMibmh0dHBzOi8vd3d3LnJldXRlcnMuY29tL3dvcmxkL2FzaWEtcGFjaWZpYy90eXBob29uLWRva3N1cmktc2h1dHMtYnVzaW5lc3Nlcy1ncm91bmRzLWZsaWdodHMtdGFpd2FuLTIwMjMtMDctMjcv0gEA?oc=5&hl=en-SG&gl=SG&ceid=SG:en
An error occurred while fetching the article: Article `download()` failed with 403 Client Error: Forbidden for url: https://www.ajot.com/news/haropa-port-work-starts-on-electrical-power-supplies-to-ships-at-berth-le-havre-cruise-terminal on URL https://news.google.com/rss/articles/CBMieWh0dHBzOi8vd3d3LmFqb3QuY29tL25ld3MvaGFyb3BhLXBvcnQtd29yay1zdGFydHMtb24tZWxlY3RyaWNhbC1wb3dlci1zdXBwbGllcy10by1zaGlwcy1hdC1iZXJ0aC1sZS1oYXZyZS1jcnVpc2UtdGVybWluYWzSAQA?oc=5&hl=en-SG&gl=SG&ceid=SG:en
An error occurred while fetching the article: Artic

03/11/2024 11:45:14 AM - fromstring() returned an invalid string: 
<!doctype html>
<h...


...

An error occurred while fetching the article: Article `download()` failed with 403 Client Error: Forbidden for url: https://vancouversun.com/news/local-news/bc-windstorm-knocks-out-power-for-thousands on URL https://news.google.com/rss/articles/CBMiVGh0dHBzOi8vdmFuY291dmVyc3VuLmNvbS9uZXdzL2xvY2FsLW5ld3MvYmMtd2luZHN0b3JtLWtub2Nrcy1vdXQtcG93ZXItZm9yLXRob3VzYW5kc9IBggFodHRwczovL3ZhbmNvdXZlcnN1bi5jb20vbmV3cy9sb2NhbC1uZXdzL2JjLXdpbmRzdG9ybS1rbm9ja3Mtb3V0LXBvd2VyLWZvci10aG91c2FuZHMvd2NtLzg3ZTJjMzY3LWNkOGMtNDBlMi04NGVmLTU5MTU4NWEwODRiNy9hbXAv?oc=5&hl=en-SG&gl=SG&ceid=SG:en


03/11/2024 04:46:55 PM - fromstring() returned an invalid string: <!doctype html><html...
03/11/2024 04:46:55 PM - fromstring() returned an invalid string: <!DOCTYPE html>
<htm...


An error occurred while fetching the article: Article `download()` failed with 403 Client Error: Forbidden for url: https://www.worldvision.org/disaster-relief-news-stories/2013-typhoon-haiyan-facts on URL https://news.google.com/rss/articles/CBMiUmh0dHBzOi8vd3d3LndvcmxkdmlzaW9uLm9yZy9kaXNhc3Rlci1yZWxpZWYtbmV3cy1zdG9yaWVzLzIwMTMtdHlwaG9vbi1oYWl5YW4tZmFjdHPSAQA?oc=5&hl=en-SG&gl=SG&ceid=SG:en
An error occurred while fetching the article: Article `download()` failed with 403 Client Error: Forbidden for url: https://www.ajot.com/news/resilience360-research-shows-impacts-of-labor-disputes-at-australian-ports on URL https://news.google.com/rss/articles/CBMiZGh0dHBzOi8vd3d3LmFqb3QuY29tL25ld3MvcmVzaWxpZW5jZTM2MC1yZXNlYXJjaC1zaG93cy1pbXBhY3RzLW9mLWxhYm9yLWRpc3B1dGVzLWF0LWF1c3RyYWxpYW4tcG9ydHPSAQA?oc=5&hl=en-SG&gl=SG&ceid=SG:en
An error occurred while fetching the article: Article `download()` failed with 403 Client Error: Forbidden for url: https://www.ajot.com/news/resilience360-research-shows

03/11/2024 04:50:14 PM - fromstring() returned an invalid string: 			<!DOCTYPE html>
	...


An error occurred while fetching the article: Article `download()` failed with 403 Client Error: Forbidden for url: https://www.oecd.org/coronavirus/policy-responses/the-territorial-impact-of-covid-19-managing-the-crisis-across-levels-of-government-d3e314e1/ on URL https://news.google.com/rss/articles/CBMijgFodHRwczovL3d3dy5vZWNkLm9yZy9jb3JvbmF2aXJ1cy9wb2xpY3ktcmVzcG9uc2VzL3RoZS10ZXJyaXRvcmlhbC1pbXBhY3Qtb2YtY292aWQtMTktbWFuYWdpbmctdGhlLWNyaXNpcy1hY3Jvc3MtbGV2ZWxzLW9mLWdvdmVybm1lbnQtZDNlMzE0ZTEv0gEA?oc=5&hl=en-SG&gl=SG&ceid=SG:en
An error occurred while fetching the article: Article `download()` failed with 403 Client Error: Forbidden for url: https://www.iol.co.za/dailynews/news/strong-winds-leads-to-traffic-congestion-on-bayhead-road-34984869 on URL https://news.google.com/rss/articles/CBMiZmh0dHBzOi8vd3d3LmlvbC5jby56YS9kYWlseW5ld3MvbmV3cy9zdHJvbmctd2luZHMtbGVhZHMtdG8tdHJhZmZpYy1jb25nZXN0aW9uLW9uLWJheWhlYWQtcm9hZC0zNDk4NDg2OdIBAA?oc=5&hl=en-SG&gl=SG&ceid=SG:en
An error occurred while 

In [ ]:
print(datetime.datetime.now())

In [11]:
tes

id                                           Headline  \
0        1.0  Grasberg Mine- Grasberg mine workers extend st...   
1        2.0  Indonesia: Undersea internet cables damaged by...   
2        3.0  Shanghai port congestion impacts terminals in ...   
3        4.0  UPDATE - Indonesia: Explosion at KP Terminal i...   
4        5.0  UPDATE - Indonesia: Police confirm two explosi...   
...      ...                                                ...   
5777  5776.0  Winter storm may bring inclement weather condi...   
5778  5777.0  Winter weather expected to continue to impact ...   
5779  5778.0  Workers of Svitzer Australia plan to strike on...   
5780  5779.0  Workers stage 24-hour stoppage at DP World Ter...   
5781  5780.0  Workers with Ertsoverslagbedrijf Europoort C.V...   

                                                Details  Severity  \
0     Media sources indicate that workers at the Gra...  Moderate   
1     News sources are stating that recent typhoons ...     Minor   
2     The persisting port congestion at Shanghai’s Y...     Minor   
3     Updated local media sources from Jakarta indic...   Extreme   
4     According to local police in Jakarta, two expl...   Extreme   
...                                                 ...       ...   
5777  Intelligence received by Everstream Analytics ...  Moderate   
5778  Meteorological sources indicate that a series ...     Minor   
5779  Industry sources report on December 7 that Svi...  Moderate   
5780  Industry sources indicate on December 14 that ...  Moderate   
5781  On November 17, Dutch media sources reported t...     Minor   

                                               Category         Region  \
0                                   Mine Workers Strike      Indonesia   
1                                        Travel Warning      Indonesia   
2                                       Port Congestion          China   
3                            Bombing, Police Operations      Indonesia   
4                            Bombing, Police Operations      Indonesia   
...                                                 ...            ...   
5777                                          Ice Storm  United States   
5778  Roadway Closure / Disruption, Ground Transport...  United States   
5779                                  Industrial Action      Australia   
5780                                        Port Strike      Australia   
5781                                        Port Strike    Netherlands   

            Datetime    Year       lat        lon maritime_label  \
0      28/5/17 17:08  2017.0  -4.05608  137.11302          False   
1       4/9/17 14:30  2017.0       NaN        NaN          False   
2       27/4/17 9:16  2017.0  29.52000  121.33190           True   
3      24/5/17 15:15  2017.0  -6.22465  106.86700           True   
4      24/5/17 16:20  2017.0       NaN        NaN           True   
...              ...     ...       ...        ...            ...   
5777   16/12/20 2:47  2020.0  38.90072  -77.05440          False   
5778  31/12/20 18:15  2020.0  41.30357  -72.90561          False   
5779    7/12/20 6:16  2020.0 -38.35169  145.25050          False   
5780  14/12/20 16:52  2020.0       NaN        NaN           True   
5781  18/11/20 17:55  2020.0  51.96121    4.10550          False   

                            found_ports  contains_port_info if_labeled  Month  \
0                          ['freeport']                 1.0      False    5.0   
1                         ['hong kong']                 1.0      False    4.0   
2     ['ningbo', 'qingdao', 'shanghai']                 1.0      False    4.0   
3                           ['jakarta']                 1.0      False    5.0   
4                           ['jakarta']                 1.0       True    5.0   
...                                 ...                 ...        ...    ...   
5777                       ['new york']                 1.0      False   12.0   
5778           ['new y

In [15]:
count_rows = tes[
    ~tes["content"].isin(["cannot scrape the content", "no content found"])
].shape[0]
count_rows

3429

In [16]:
count_rows = tes[tes["content"].isin(["no content found"])].shape[0]
count_rows

2155

In [17]:
count_rows = tes[tes["content"].isin(["cannot scrape the content"])].shape[0]
count_rows

126

In [12]:
tes.to_parquet("scraped_data1.parquet", index=False)
tes.to_csv("scraped_data1.csv", index=False)